In [124]:
import pandas as pd
import ast
from sklearn.metrics.pairwise import cosine_similarity

In [125]:
# importing the dataset
categories = pd.read_csv('data/item_categories.csv')
item_daily_features = pd.read_csv('data/item_daily_features.csv')
# to test our model
interactions = pd.read_csv('data/small_matrix.csv')

In [126]:
for i in range (31):
    categories['category_' + str(i)] = 0

categories['feat'] = categories['feat'].apply(ast.literal_eval)
for index, row in categories.iterrows():
    # Get the list of features for the current row
    features = row['feat']

    # Set the corresponding category columns to 1
    for feat in features:
        col_name = f'category_{feat}'
        if col_name in categories.columns:
            categories.at[index, col_name] = 1
categories.drop(columns=['feat'], inplace=True)
categories

video_id  category_0  category_1  category_2  category_3  category_4  \
0             0           0           0           0           0           0   
1             1           0           0           0           0           0   
2             2           0           0           0           0           0   
3             3           0           0           0           0           0   
4             4           0           0           0           0           0   
...         ...         ...         ...         ...         ...         ...   
10723     10723           0           0           0           0           0   
10724     10724           0           0           1           0           0   
10725     10725           0           0           0           0           0   
10726     10726           0           0           0           0           0   
10727     10727           0           0           0           0           0   

       category_5  category_6  category_7  category_8  ...  category_21  \
0               0           0           0           1  ...            0   
1               0           0           0           0  ...            0   
2               0           0           0           0  ...            0   
3               0           0           0           0  ...            0   
4               1           0           0           0  ...            0   
...           ...         ...         ...         ...  ...          ...   
10723           0           0           0           0  ...            0   
10724           0           0           0           0  ...            0   
10725           0           0           0           0  ...            0   
10726           0           0           0           0  ...            0   
10727           1           0           0           0  ...            0   

       category_22  category_23  category_24  category_25  category_26  \
0                0            0            0            0            0   
1                0            0            0            0            0   
2                0            0            0            0            0   
3                0            0            0            0            1   
4                0            0            0            0            0   
...            ...          ...          ...          ...          ...   
10723            0            0            0            0            0   
10724            0            0            0            0            0   
10725            0            0            0            0            0   
10726            0            0            0            0            0   
10727            0            0            0            0            0   

       category_27  category_28  category_29  category_30  
0                0            0            0            0  
1                1            0            0            0  
2                0            0            0            0  
3                0            0            0            0  
4                0            0            0            0  
...            ...          ...          ...          ...  
10723            0            0            0            0  
10724            0            0            0            0  
10725            0            0            0            0  
10726            0            0            0            0  
10727            0            0            0            0  

[10728 rows x 32 columns]

In [151]:
video_metadata = item_daily_features[['video_id', 'author_id', 'video_type', 'upload_dt', 'visible_status', 'video_duration', 'video_width', 'video_height', 'music_id']] # maybe add upload_type
# I only want one row per video_id
video_metadata = video_metadata.drop_duplicates(subset=['video_id'])

# Convert video type to int meaning if it is AD it is 0 and if it is NORMAL 1
video_metadata['video_type'] = video_metadata['video_type'].apply(lambda x: 1 if x == 'NORMAL' else 0)
video_metadata['visible_status'] = video_metadata['visible_status'].apply(lambda x: 1 if x == 'public' else 0)
video_metadata['upload_dt'] = pd.to_datetime(video_metadata['upload_dt'], format='%Y-%m-%d')
video_metadata['upload_dt'] = video_metadata['upload_dt'].astype('int64') // 10**9
video_metadata.dropna(inplace=True)
# # convert datetime to unix timestamp
# metadata.dtypes
# video_metadata['id'] = video_metadata['video_id']
# video_metadata.set_index('video_id', inplace=True)
# Change the index to increment from 0 to n
video_metadata.reset_index(drop=True, inplace=True)
video_metadata
# merge video metadata with categories
video_metadata = video_metadata.merge(categories, on='video_id', how='left')
video_metadata


video_id  author_id  video_type   upload_dt  visible_status  \
0             0       3309           1  1585526400               1   
1             2        939           1  1586563200               1   
2             4       4284           1  1586649600               1   
3             5       3483           1  1586908800               1   
4             6        725           1  1586908800               1   
...         ...        ...         ...         ...             ...   
10433     10723        236           1  1599264000               1   
10434     10724       5271           1  1599264000               1   
10435     10725       1924           1  1599264000               1   
10436     10726       7604           1  1599264000               1   
10437     10727       7464           1  1599264000               1   

       video_duration  video_width  video_height    music_id  category_0  ...  \
0              5966.0          720          1280  3350323409           0  ...   
1              8000.0          720          1280           0           0  ...   
2             18000.0          720          1280  3442844592           0  ...   
3              8000.0          720           720  2457773462           0  ...   
4              6000.0          720          1280  3393422084           0  ...   
...               ...          ...           ...         ...         ...  ...   
10433          4833.0          720          1280  4428603493           0  ...   
10434         54720.0          720          1280  1090207430           0  ...   
10435         15800.0          576          1024  4429406509           0  ...   
10436          5132.0          528           960       68154           0  ...   
10437          5666.0          720          1556  1090827283           0  ...   

       category_21  category_22  category_23  category_24  category_25  \
0                0            0            0            0            0   
1                0            0            0            0            0   
2                0            0            0            0            0   
3                0            0            0            0            0   
4                0            0            0            0            0   
...            ...          ...          ...          ...          ...   
10433            0            0            0            0            0   
10434            0            0            0            0            0   
10435            0            0            0            0            0   
10436            0            0            0            0            0   
10437            0            0            0            0            0   

       category_26  category_27  category_28  category_29  category_30  
0                0            0            0            0            0  
1                0            0            0            0            0  
2                0            0            0            0            0  
3                0            0            0            0            0  
4                0            0            0            0            0  
...            ...          ...          ...          ...          ...  
10433            0            0            0            0            0  
10434            0            0            0            0            0  
10435            0            0            0            0            0  
10436            0            0            0            0            0  
10437            0            0            0            0            0  

[10438 rows x 40 columns]

In [152]:
# compute the cosine similarity of the videos
similarity = cosine_similarity(video_metadata.iloc[:, 1:])

In [153]:
def get_recommendations(video_id, similarity, video_vector, top_n=5):
    idx = video_vector[video_vector['video_id'] == video_id].index
    if len(idx) == 0:
        return []
    similarity_scores = list(enumerate(similarity[idx[0]]))
     # Sort the similarity scores in descending order
    similarity_scores = sorted(similarity_scores, key=lambda x: x[1], reverse=True)
     # Get the top_n movie indices
    movie_indices = [i[0] for i in similarity_scores[1:top_n+1]]
    return video_vector['video_id'].iloc[movie_indices].values.tolist()

In [160]:
import dtale
reco = get_recommendations(0, similarity, video_metadata, 5)
test2 = get_video_metadata(reco, video_metadata)
dtale.show(test2)

In [155]:
def generate_test(n, video_vector, interactions):
    ids = video_vector['video_id'].values.tolist()
    print(f'Number of videos: {len(ids)}')
    print(f'Number of unique videos: {len(interactions["video_id"].unique())}')
    test_df = interactions[interactions['video_id'].isin(ids)]
    print(f'Number of unique videos: {len(interactions["video_id"].unique())}')
    test_df = interactions[['user_id', 'video_id', 'watch_ratio']]
    test_df = test_df.dropna()
    # print(test_df)
    test_df = test_df.groupby(['user_id']).apply(lambda x: x.nlargest(n, 'watch_ratio')).reset_index(drop=True)
    test_df = test_df.set_index(['user_id', 'video_id'])
    return test_df

generate_test(5, video_metadata, interactions)

Number of videos: 10438
Number of unique videos: 3327
Number of unique videos: 3327


/tmp/ipykernel_128763/304603087.py:10: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  test_df = test_df.groupby(['user_id']).apply(lambda x: x.nlargest(n, 'watch_ratio')).reset_index(drop=True)


watch_ratio
user_id video_id             
14      10200       26.705261
        9157        19.091856
        1386        16.313334
        4715        13.223575
        1933        12.667778
...                       ...
7162    8298         5.093884
        554          4.586923
        7191         4.394391
        600          4.387822
        768          4.273151

[7055 rows x 1 columns]

In [156]:
# Get the row in video_metadata for video_id 10200, 9157, 1386, 4715, 1933
def get_video_metadata(video_id, video_metadata):
    video_metadata = video_metadata[video_metadata['video_id'].isin(video_id)]
    return video_metadata
test = [10200, 9157, 1386, 4715, 1933]
test1 = get_video_metadata(test, video_metadata)
test1

video_id  author_id  video_type   upload_dt  visible_status  \
1340      1386       7905           1  1597795200               1   
1884      1933       5640           1  1593734400               1   
4589      4715       4130           1  1597795200               1   
8900      9157        171           1  1597881600               1   
9917     10200       2702           1  1596585600               1   

      video_duration  video_width  video_height    music_id  category_0  ...  \
1340          6966.0          720          1280  4324352685           0  ...   
1884          7199.0          720          1282           0           0  ...   
4589          5666.0          719          1280  4003609143           0  ...   
8900          5933.0          720          1280  2867362602           0  ...   
9917          9275.0          576          1024  4229597123           0  ...   

      category_21  category_22  category_23  category_24  category_25  \
1340            0            0            0            0            0   
1884            0            0            0            0            0   
4589            0            0            0            0            0   
8900            0            0            0            0            0   
9917            0            0            0            0            0   

      category_26  category_27  category_28  category_29  category_30  
1340            0            0            1            0            0  
1884            0            0            1            0            0  
4589            0            0            0            0            0  
8900            0            0            0            0            0  
9917            0            0            0            0            0  

[5 rows x 40 columns]

In [157]:
def evaluate_recommendation_system(df, recommend, similarity, categories, top_n=5):
    precision_list = []
    recall_list = []

    # Group by user
    for user_id, group in df.groupby(level=0):
        # Sort the group by watch_ratio descending
        user_videos = group.sort_values(by='watch_ratio', ascending=False)
        
        if len(user_videos) < 2:
            continue  # Not enough data to evaluate
        
        # Get top video (used as input to model)
        input_video_id = user_videos.index[0][1]
        
        # Get top-4 videos excluding the input one => Ground truth
        ground_truth = user_videos.iloc[1:top_n].index.get_level_values(1).tolist()
        
        # Get top-4 recommended videos from the model
        recommended = recommend(input_video_id, similarity, categories, top_n)
        
        # Remove input_video_id from the recommended list if ivideo_vectort's present
        recommended = [vid for vid in recommended if vid != input_video_id][:top_n - 1]
        print(f"User ID: {user_id}")
        print(f"Input video ID: {input_video_id}")
        print(f"Ground truth: {ground_truth}")
        print(f"Recommended: {recommended}")

        # Compute intersection
        common = set(ground_truth).intersection(set(recommended))

        # Precision = correct / recommended (4)
        precision = len(common) / (top_n - 1)
        precision_list.append(precision)

        # Recall = correct / relevant (min(4, len(ground_truth)))
        recall = len(common) / min(top_n - 1, len(ground_truth))
        recall_list.append(recall)

    # Compute averages
    avg_precision = sum(precision_list) / len(precision_list) if precision_list else 0
    avg_recall = sum(recall_list) / len(recall_list) if recall_list else 0

    return avg_precision, avg_recall

In [158]:
test_df = generate_test(500, video_metadata, interactions)
precision, recal = evaluate_recommendation_system(test_df, get_recommendations, similarity, video_metadata, top_n=500)
print(f"Precision: {precision:.4f}")
print(f"Recall: {recal:.4f}")

Number of videos: 10438
Number of unique videos: 3327
Number of unique videos: 3327


/tmp/ipykernel_128763/304603087.py:10: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  test_df = test_df.groupby(['user_id']).apply(lambda x: x.nlargest(n, 'watch_ratio')).reset_index(drop=True)


User ID: 14
Input video ID: 10200
Ground truth: [9157, 1386, 4715, 1933, 2589, 5539, 10009, 847, 520, 8800, 10019, 2117, 9053, 2970, 646, 839, 10328, 8176, 6808, 1346, 4182, 2522, 2336, 5818, 1399, 2237, 10410, 9829, 300, 7670, 2133, 389, 803, 9830, 5811, 6001, 314, 4040, 9804, 7508, 7300, 8504, 2223, 2021, 5205, 557, 7098, 9991, 7305, 7266, 4020, 8783, 9572, 2128, 1305, 5693, 8766, 8291, 848, 7695, 5421, 4184, 6977, 2046, 8799, 2428, 2125, 6222, 601, 2427, 4051, 3105, 5753, 738, 2292, 4644, 619, 2894, 9178, 10519, 7047, 4189, 154, 7167, 8228, 5643, 2735, 5995, 3979, 4123, 600, 9695, 5690, 2528, 7303, 669, 4201, 3590, 5572, 361, 6293, 5668, 8524, 3917, 3344, 2413, 206, 621, 1187, 672, 4015, 4516, 137, 563, 3947, 3628, 4689, 10172, 4637, 9798, 9261, 3072, 4732, 4001, 3211, 624, 673, 3946, 1951, 1911, 1372, 7166, 5528, 1912, 8538, 576, 6787, 2178, 9965, 7501, 7014, 727, 9933, 9964, 5732, 2396, 217, 627, 2137, 203, 599, 4234, 5491, 4033, 10206, 7181, 4099, 774, 4230, 4590, 8707, 3649, 226